In [1]:
import tensorflow as tf
from tensorflow import keras
import numpy as np

In [2]:
%load_ext tensorboard

In [3]:
%tensorboard --logdir logs

Reusing TensorBoard on port 6006 (pid 9822), started 1:13:32 ago. (Use '!kill 9822' to kill it.)

In [4]:
fashion_mnist = keras.datasets.mnist

(train_images, train_labels), (test_images, test_labels) = fashion_mnist.load_data()
train_shape = train_images.shape
test_shape = test_images.shape

y_shape = len(set(train_labels))

train_images_reshaped = train_images.reshape(train_shape[0],train_shape[1]*train_shape[2])/255.0
test_images_reshaped = test_images.reshape(test_shape[0],train_images_reshaped.shape[1])/255.0

In [5]:
hidden_sizes = [1000,1000,500,200]

In [6]:
tf.reset_default_graph()

with tf.device("/CPU:0"):
    
    with tf.name_scope("input_data"):
        x_placeholder = tf.placeholder(tf.float32,shape = (None,train_shape[1]*train_shape[2]),name="X")
        y_placeholder = tf.placeholder(tf.int64,shape=(None),name="Y")
    weight_prune_k = tf.placeholder(tf.float32,shape = () ,name = "weight_prune_k")
    output_layer_weights =  tf.Variable( tf.truncated_normal([hidden_sizes[-1],y_shape]))


    weights_matrices = []
    layer_outputs = []
    weights_magnitudes_matrices = []
    top_indices_list = []
    prunned_weight_matrices = []
    prunned_layer_outputs = []
    weights_to_prune_matrices = []

    layer_outputs.append(x_placeholder)
    prunned_layer_outputs.append(x_placeholder)

    for layer in range(len(hidden_sizes)):
        
        layer_identifier = "layer_{}".format(layer)
        if layer == 0:

            prev_units = int(x_placeholder.shape[1]) 
        else:
            prev_units = int(weights_matrices[layer-1].shape[1])

        layer_units = hidden_sizes[layer]

        print(layer+1, (prev_units,layer_units))
        with tf.name_scope(layer_identifier):
            weights_matrix_l = tf.Variable( tf.truncated_normal ([prev_units,layer_units]),name = layer_identifier+"_weights")
            layer_output =  tf.nn.relu( tf.matmul(layer_outputs[layer],weights_matrix_l),name = layer_identifier+"_output")

        layer_total_weights = tf.size(weights_matrix_l)
        layer_weights_to_prune =  tf.cast(tf.floor( 
                                    tf.multiply(tf.cast(layer_total_weights,tf.float32),weight_prune_k)),tf.int32)
        weights_magnitudes = tf.abs(weights_matrix_l)
        top_values, top_indices = tf.nn.top_k(tf.reshape(-weights_magnitudes, (-1,)), layer_weights_to_prune)
        #top_indices = tf.stack(((top_indices // weights_magnitudes.shape[1]), (top_indices % weights_magnitudes.shape[1])), -1)
        top_indices = tf.stack(((top_indices // weights_magnitudes.shape[1]), (top_indices % weights_magnitudes.shape[1])), -1)
        #test_indices = tf.constant([[0,0],[6,5]])
        #test_weights_to_prune = 2
        with tf.control_dependencies([weights_matrix_l,top_indices]):
        #weights_copy_l = tf.stop_gradient(tf.Variable(tf.identity(weights_matrix_l)))
            #weights_copy_l = tf.Variable(tf.identity(weights_matrix_l),trainable = False)
            with tf.name_scope("prunned_model_"+layer_identifier) as prunned_scope:
                weights_copy_l = tf.Variable(weights_matrix_l.read_value(),trainable=False,name = layer_identifier+"_weights_copy")
            #prunned_weights_l = weights_copy_l 
        #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,[[1,1],[1,2]],[0,0])
        #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,top_indices, tf.zeros(shape=(top_indices.shape[0])))
                prunned_weights_l = tf.scatter_nd_update(weights_copy_l,top_indices, tf.zeros(shape=(layer_weights_to_prune))) #this one
                #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,test_indices, tf.zeros(shape=(test_weights_to_prune))) 
            
                #prunned_weights_l = tf.scatter_nd_update(weights_copy_l,[[0,0],[4,5]], tf.zeros(shape=(2))) 
            with tf.name_scope(prunned_scope):
                prunned_layer_output = tf.nn.relu(tf.matmul(prunned_layer_outputs[layer],prunned_weights_l))
        
        weights_matrices.append(weights_matrix_l)
        layer_outputs.append(layer_output)
        weights_magnitudes_matrices.append(weights_magnitudes)
        top_indices_list.append(top_indices)
        prunned_weight_matrices.append(prunned_weights_l)
        prunned_layer_outputs.append(prunned_layer_output)
        weights_to_prune_matrices.append(layer_weights_to_prune)

    last_layer_output =    tf.matmul(  layer_output , output_layer_weights)
    last_prunned_layer_output = tf.matmul(prunned_layer_output,output_layer_weights,name="prunned_output")
    last_prunned_layer_soft_output = tf.nn.softmax(last_prunned_layer_output)
    last_prunned_layer_hard_output = tf.argmax(last_prunned_layer_soft_output,axis = 1)

    print(layer+2,  (hidden_sizes[-1],y_shape))

    loss =  tf.reduce_mean(
        tf.nn.sparse_softmax_cross_entropy_with_logits(labels = y_placeholder,logits = last_layer_output))
    optimizer_step = tf.train.AdamOptimizer(0.01).minimize(loss)

    last_layer_hard_output = tf.argmax(last_layer_output,axis=1)
    accuracy = tf.reduce_mean( tf.cast( tf.equal(last_layer_hard_output,y_placeholder),tf.float32))
    prunned_accuracy = tf.reduce_mean(tf.cast(tf.equal(last_prunned_layer_hard_output,y_placeholder),tf.float32))


    init = tf.global_variables_initializer()

W0625 19:55:07.758908 4686321088 deprecation.py:323] From /Users/llealhernandez/anaconda3/envs/tf/lib/python3.7/site-packages/tensorflow/python/ops/variables.py:2618: Variable.initialized_value (from tensorflow.python.ops.variables) is deprecated and will be removed in a future version.
Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.


1 (784, 1000)
2 (1000, 1000)
3 (1000, 500)
4 (500, 200)
5 (200, 10)


In [7]:
EPOCHS = 2
PRINT_EVERY = 1

In [8]:
config = tf.ConfigProto(allow_soft_placement = True)
sess = tf.InteractiveSession(config=config)

In [9]:
train_writer = tf.summary.FileWriter( './logs/', sess.graph)

sess.run(init)
feed_dict = {x_placeholder:train_images_reshaped,y_placeholder:train_labels}

for epoch in range(1,EPOCHS + 1):
    _,epoch_loss,epoch_output,epoch_hard_output,epoch_acc  = sess.run([optimizer_step,loss,last_layer_output,last_layer_hard_output,accuracy],feed_dict)
    
    if epoch % PRINT_EVERY == 0:
        print("Epoch :{} loss:{}  epoch acc:{}".format(epoch,epoch_loss,epoch_acc))
        

trained_weights =  sess.run([layer  for layer in  weights_matrices],feed_dict=feed_dict)


Epoch :1 loss:444183.84375  epoch acc:0.11646666377782822
Epoch :2 loss:474229.0625  epoch acc:0.23309999704360962


In [10]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.1}
test_acc = sess.run(accuracy,feed_dict=test_feed_dict)

print("Test acc",test_acc)


Test acc 0.3211


In [11]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.2}
sess.run(prunned_accuracy,feed_dict=test_feed_dict)

0.2161

In [12]:
layer_to_verify = 0
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:0.00002}
out,i , test_weights_matrices, test_prunned_matrices ,to_prune_count= sess.run([last_prunned_layer_hard_output,top_indices_list[layer_to_verify],weights_matrices[layer_to_verify],prunned_weight_matrices[layer_to_verify],weights_to_prune_matrices[layer_to_verify]],feed_dict=test_feed_dict)


In [13]:
set(out)

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9}

In [14]:
i

array([[191, 749],
       [156, 593],
       [317, 997],
       [142, 436],
       [375, 217],
       [521, 349],
       [241, 273],
       [114, 455],
       [723, 561],
       [668, 976],
       [750, 582],
       [480, 373],
       [401, 540],
       [118, 823],
       [356, 598]], dtype=int32)

In [15]:
test_weights_matrices

array([[-1.5410141 , -0.6974524 ,  1.3204434 , ..., -0.84221447,
        -0.44060287, -0.5080981 ],
       [ 1.1425743 ,  0.24068497,  1.9254318 , ...,  1.4547498 ,
         1.4006408 ,  0.5559119 ],
       [-0.39473048, -0.4631712 ,  1.3944118 , ...,  0.07255328,
         1.3733389 ,  1.0941644 ],
       ...,
       [-0.31637   , -0.56183505, -0.7364273 , ..., -0.65186733,
         0.06325265,  0.93998885],
       [-0.18222338,  0.37751406,  1.1475929 , ...,  0.8483233 ,
        -0.21423669, -0.64344645],
       [ 1.2469388 ,  0.39688224, -0.3857689 , ..., -1.4246123 ,
        -0.787072  ,  0.18425313]], dtype=float32)

In [16]:
np.min(np.abs(test_weights_matrices))

2.058252e-06

In [17]:
test_weights_matrices[40][130]

0.75673634

In [18]:
test_prunned_matrices

array([[-1.5410141 , -0.6974524 ,  1.3204434 , ..., -0.84221447,
        -0.44060287, -0.5080981 ],
       [ 1.1425743 ,  0.        ,  1.9254318 , ...,  1.4547498 ,
         1.4006408 ,  0.5559119 ],
       [-0.39473048, -0.4631712 ,  1.3944118 , ...,  0.        ,
         1.3733389 ,  1.0941644 ],
       ...,
       [-0.31637   , -0.56183505, -0.7364273 , ..., -0.65186733,
         0.        ,  0.93998885],
       [ 0.        ,  0.37751406,  1.1475929 , ...,  0.8483233 ,
         0.        , -0.64344645],
       [ 1.2469388 ,  0.39688224, -0.3857689 , ..., -1.4246123 ,
        -0.787072  ,  0.        ]], dtype=float32)

In [19]:
equal_matrix = test_weights_matrices == test_prunned_matrices
for i in range(test_weights_matrices.shape[0]):
    for j in range(test_prunned_matrices.shape[1]):
        if not equal_matrix[i][j]  and test_prunned_matrices[i][j] == 0:
            print(i,j, test_weights_matrices[i][j] ,test_prunned_matrices[i][j])



0 4 -0.05044583 0.0
0 5 -0.062717766 0.0
0 6 0.054805204 0.0
0 9 0.025915848 0.0
0 11 0.1815879 0.0
0 14 0.21790887 0.0
0 21 0.12851615 0.0
0 24 0.08132125 0.0
0 25 0.23062024 0.0
0 32 -0.1812605 0.0
0 35 -0.16306795 0.0
0 48 -0.19019233 0.0
0 50 0.016224364 0.0
0 53 0.1792261 0.0
0 62 -0.12748146 0.0
0 72 0.16889174 0.0
0 73 0.21554832 0.0
0 80 0.022629758 0.0
0 84 0.1985376 0.0
0 85 -0.072987996 0.0
0 92 -0.12023618 0.0
0 95 -0.15110715 0.0
0 97 -0.08414096 0.0
0 102 -0.017386405 0.0
0 106 0.14668207 0.0
0 109 0.20175706 0.0
0 111 0.08459603 0.0
0 112 0.20455185 0.0
0 113 -0.19883159 0.0
0 118 -0.1458913 0.0
0 119 0.19200052 0.0
0 121 0.011366676 0.0
0 129 -0.1802654 0.0
0 130 -0.19981681 0.0
0 132 -0.2255879 0.0
0 138 0.12279899 0.0
0 149 0.07305329 0.0
0 155 -0.15168133 0.0
0 156 0.12877475 0.0
0 159 0.13906494 0.0
0 167 0.18900464 0.0
0 174 0.13976923 0.0
0 179 0.0595211 0.0
0 181 -0.19596365 0.0
0 185 -0.12108115 0.0
0 186 -0.012140051 0.0
0 189 -0.09843167 0.0
0 194 0.0011093987

2 456 -0.07703281 0.0
2 459 -0.24173518 0.0
2 474 0.19368708 0.0
2 477 -0.19564325 0.0
2 488 0.12493518 0.0
2 499 0.18655175 0.0
2 502 0.24031381 0.0
2 504 0.024017297 0.0
2 515 0.1981886 0.0
2 527 0.21889569 0.0
2 531 -0.119715355 0.0
2 542 0.05088743 0.0
2 543 -0.06954222 0.0
2 544 0.1623232 0.0
2 548 0.17434607 0.0
2 549 0.030664526 0.0
2 555 -0.21929832 0.0
2 562 -0.08517681 0.0
2 569 0.01960539 0.0
2 570 -0.027026495 0.0
2 572 -0.10795334 0.0
2 579 -0.17602505 0.0
2 592 0.14072558 0.0
2 595 -0.07964049 0.0
2 598 0.093884334 0.0
2 603 0.19731212 0.0
2 607 0.13888493 0.0
2 611 -0.09962799 0.0
2 614 0.025683891 0.0
2 618 0.23595136 0.0
2 625 -0.18116927 0.0
2 630 0.018247206 0.0
2 632 0.20304672 0.0
2 633 0.21254312 0.0
2 649 -0.058167838 0.0
2 655 -0.07027299 0.0
2 660 0.09814231 0.0
2 661 -0.077986136 0.0
2 662 -0.068826124 0.0
2 664 0.14385395 0.0
2 665 -0.031898417 0.0
2 672 -0.12427195 0.0
2 682 0.041384727 0.0
2 686 0.19083932 0.0
2 687 -0.12376723 0.0
2 688 0.22531748 0.0
2 69

6 412 -0.016961215 0.0
6 435 -0.12593618 0.0
6 436 -0.15609303 0.0
6 470 0.09376783 0.0
6 471 0.17361377 0.0
6 483 -0.097084396 0.0
6 486 0.0485991 0.0
6 498 -0.18121643 0.0
6 499 -0.04591086 0.0
6 503 -0.17181681 0.0
6 505 -0.12163613 0.0
6 508 0.19388658 0.0
6 509 -0.07711451 0.0
6 513 0.19165418 0.0
6 517 -0.040128376 0.0
6 519 0.13860986 0.0
6 522 -0.1425569 0.0
6 524 -0.166957 0.0
6 526 0.039394014 0.0
6 529 -0.1338303 0.0
6 532 -0.15760647 0.0
6 536 0.15765564 0.0
6 541 -0.1401766 0.0
6 553 0.13500948 0.0
6 556 -0.22408062 0.0
6 560 -0.14128046 0.0
6 562 -0.1271095 0.0
6 569 0.095109776 0.0
6 570 0.22807945 0.0
6 572 -0.13220578 0.0
6 574 -0.11861174 0.0
6 586 -0.040234156 0.0
6 607 0.110458605 0.0
6 611 0.17442723 0.0
6 624 0.040725578 0.0
6 625 0.033107467 0.0
6 630 -0.079277955 0.0
6 631 -0.17066884 0.0
6 636 -0.07542126 0.0
6 640 0.14228614 0.0
6 646 0.04619096 0.0
6 647 -0.048253145 0.0
6 651 0.2085301 0.0
6 653 -0.20712653 0.0
6 657 -0.10571989 0.0
6 661 0.028929526 0.0
6 6

10 812 0.14360152 0.0
10 815 0.19981936 0.0
10 823 0.0030182279 0.0
10 825 0.22602905 0.0
10 837 -0.18137076 0.0
10 840 0.007634178 0.0
10 841 -0.09594247 0.0
10 844 0.118960194 0.0
10 847 0.10683747 0.0
10 848 -0.08728657 0.0
10 850 0.03490133 0.0
10 852 -0.2300006 0.0
10 854 0.017662017 0.0
10 856 0.21893845 0.0
10 861 -0.22499733 0.0
10 867 0.1278315 0.0
10 883 -0.13061973 0.0
10 886 0.12856083 0.0
10 888 -0.10560711 0.0
10 892 -0.058597498 0.0
10 900 0.14704186 0.0
10 901 0.2415331 0.0
10 903 -0.13131317 0.0
10 908 -0.23675358 0.0
10 916 0.09602521 0.0
10 917 -0.008116112 0.0
10 919 0.12854393 0.0
10 923 -0.07099205 0.0
10 930 0.09234474 0.0
10 931 -0.22825652 0.0
10 939 0.003833282 0.0
10 944 0.17451721 0.0
10 945 -0.1181897 0.0
10 962 0.085270695 0.0
10 964 -0.06113885 0.0
10 969 0.22074877 0.0
10 971 -0.14473027 0.0
10 978 -0.038374946 0.0
10 981 -0.012455885 0.0
10 982 0.15017833 0.0
10 983 -0.1500726 0.0
10 988 -0.14282408 0.0
11 14 0.052689184 0.0
11 16 0.047141224 0.0
11 28 

14 472 -0.22691514 0.0
14 479 -0.036996964 0.0
14 484 -0.18957354 0.0
14 488 -0.16296843 0.0
14 492 0.20046534 0.0
14 502 -0.053220935 0.0
14 506 -0.23066232 0.0
14 507 0.024168732 0.0
14 514 -0.081054844 0.0
14 517 0.09167353 0.0
14 526 -0.010637164 0.0
14 532 0.047574956 0.0
14 533 0.078481235 0.0
14 541 0.2132244 0.0
14 547 0.13035387 0.0
14 548 0.18843116 0.0
14 557 0.23529571 0.0
14 558 0.17272688 0.0
14 560 -0.02899276 0.0
14 565 0.15819208 0.0
14 566 0.113998376 0.0
14 568 -0.054852653 0.0
14 574 0.09141157 0.0
14 575 0.17700084 0.0
14 578 -0.0993597 0.0
14 581 0.0022421516 0.0
14 587 -0.13288054 0.0
14 598 -0.09182396 0.0
14 601 -0.07313758 0.0
14 603 -0.22222334 0.0
14 613 0.1338875 0.0
14 616 -0.11996391 0.0
14 619 -0.064897984 0.0
14 623 -0.17031442 0.0
14 625 -0.05070705 0.0
14 628 0.16824579 0.0
14 630 0.0023387773 0.0
14 638 -0.23611452 0.0
14 640 0.17315589 0.0
14 650 -0.12509996 0.0
14 651 -0.03780215 0.0
14 657 0.038283825 0.0
14 658 -0.04644508 0.0
14 661 0.18841523 0

...

768 319 0.16821021 0.0
768 322 0.09599804 0.0
768 323 0.1270052 0.0
768 327 0.21674417 0.0
768 335 0.22621214 0.0
768 338 -0.011768432 0.0
768 344 0.04684028 0.0
768 346 -0.16418089 0.0
768 349 -0.090719804 0.0
768 366 -0.10737569 0.0
768 373 0.21587919 0.0
768 380 0.16850924 0.0
768 382 0.010936871 0.0
768 385 0.13731195 0.0
768 386 0.10366643 0.0
768 426 0.22413972 0.0
768 429 -0.16723269 0.0
768 431 0.19525002 0.0
768 440 0.081816524 0.0
768 453 -0.0786678 0.0
768 455 0.1401239 0.0
768 464 0.057087015 0.0
768 466 -0.06762727 0.0
768 470 0.23579031 0.0
768 472 0.123087615 0.0
768 479 0.10858043 0.0
768 483 0.23903896 0.0
768 486 -0.22805181 0.0
768 489 -0.1712632 0.0
768 493 0.043601826 0.0
768 495 -0.23740736 0.0
768 506 -0.008411551 0.0
768 511 0.2108495 0.0
768 515 0.012927936 0.0
768 526 -0.22570215 0.0
768 532 0.103596814 0.0
768 542 0.092551045 0.0
768 548 0.2276273 0.0
768 549 -0.23557708 0.0
768 554 -0.10976887 0.0
768 556 -0.16600125 0.0
768 561 0.18407452 0.0
768 563 -0.201

771 758 0.18346983 0.0
771 759 0.05003106 0.0
771 762 0.1388904 0.0
771 768 0.16851549 0.0
771 772 -0.15964517 0.0
771 774 -0.033638 0.0
771 775 0.16156404 0.0
771 776 0.15756264 0.0
771 801 0.20043786 0.0
771 804 0.10681606 0.0
771 805 0.22617397 0.0
771 812 -0.17610577 0.0
771 814 -0.171889 0.0
771 817 0.20180714 0.0
771 819 0.11791911 0.0
771 822 -0.20025395 0.0
771 826 -0.23255503 0.0
771 828 -0.010845242 0.0
771 830 0.12321018 0.0
771 835 0.11697367 0.0
771 846 -0.06412746 0.0
771 847 0.06640877 0.0
771 854 -0.05413853 0.0
771 864 -0.1433678 0.0
771 871 -0.014671703 0.0
771 872 0.20318733 0.0
771 880 -0.102872774 0.0
771 881 0.16128229 0.0
771 882 0.2265865 0.0
771 883 0.08820063 0.0
771 886 0.0014994196 0.0
771 887 0.05751917 0.0
771 889 0.21871303 0.0
771 893 -0.106303155 0.0
771 894 0.10725533 0.0
771 896 0.1868697 0.0
771 903 0.16673043 0.0
771 907 -0.068365514 0.0
771 908 -0.05287458 0.0
771 910 -0.043377455 0.0
771 925 -0.14630164 0.0
771 931 -0.054245573 0.0
771 942 -0.1012

775 689 -0.032010548 0.0
775 691 -0.059615035 0.0
775 695 -0.22091933 0.0
775 696 -0.1587409 0.0
775 705 0.19211243 0.0
775 713 -0.14842927 0.0
775 714 0.13894546 0.0
775 718 0.1887037 0.0
775 722 0.110586 0.0
775 725 -0.16155188 0.0
775 727 -0.053289644 0.0
775 729 -0.062715106 0.0
775 744 -0.22320062 0.0
775 749 -0.036395524 0.0
775 754 -0.080416314 0.0
775 768 -0.055874843 0.0
775 774 -0.15120618 0.0
775 781 0.113664046 0.0
775 794 0.21704677 0.0
775 797 -0.16940416 0.0
775 799 0.060690224 0.0
775 805 0.122848324 0.0
775 819 -0.08236976 0.0
775 830 -0.15035337 0.0
775 836 0.2315913 0.0
775 841 0.022919271 0.0
775 864 0.098334625 0.0
775 866 -0.19312851 0.0
775 886 0.2363293 0.0
775 890 -0.017197317 0.0
775 892 -0.050225493 0.0
775 895 -0.20375472 0.0
775 901 0.065807134 0.0
775 904 -0.21826729 0.0
775 909 -0.13017978 0.0
775 917 0.021582877 0.0
775 923 -0.19360058 0.0
775 925 -0.21432053 0.0
775 927 0.0041323 0.0
775 935 0.15719451 0.0
775 937 0.17974712 0.0
775 950 -0.20851457 0.0


779 401 0.06943259 0.0
779 403 0.101398975 0.0
779 405 0.025247118 0.0
779 407 0.06419997 0.0
779 410 -0.01983054 0.0
779 411 0.07529956 0.0
779 412 -0.0014171106 0.0
779 415 -0.17487098 0.0
779 416 0.1506761 0.0
779 424 -0.09904499 0.0
779 429 0.045739386 0.0
779 430 -0.183236 0.0
779 431 0.07756506 0.0
779 436 0.20191243 0.0
779 467 0.116473824 0.0
779 481 0.13272196 0.0
779 482 0.050527334 0.0
779 486 -0.001962257 0.0
779 487 0.03476607 0.0
779 489 0.073862 0.0
779 495 0.04050306 0.0
779 499 -0.073079355 0.0
779 500 0.0501266 0.0
779 526 0.2121094 0.0
779 527 -0.22879063 0.0
779 528 0.024821103 0.0
779 542 -0.19547173 0.0
779 543 -0.23272535 0.0
779 546 -0.2020727 0.0
779 548 -0.007655493 0.0
779 549 -0.04075106 0.0
779 551 0.03733332 0.0
779 552 -0.14119618 0.0
779 555 0.08007728 0.0
779 559 -0.20039286 0.0
779 562 0.0095890835 0.0
779 569 0.18683931 0.0
779 574 -0.082264364 0.0
779 583 -0.038849667 0.0
779 584 0.23723006 0.0
779 585 -0.16792844 0.0
779 586 0.12714703 0.0
779 587 -

783 38 0.01972405 0.0
783 42 -0.091660425 0.0
783 45 -0.22323197 0.0
783 47 0.13056108 0.0
783 53 0.093614385 0.0
783 60 0.06396941 0.0
783 62 -0.14858522 0.0
783 63 0.13636371 0.0
783 66 -0.00058436923 0.0
783 70 -0.015044769 0.0
783 73 0.075890675 0.0
783 74 -0.23132123 0.0
783 78 0.11262003 0.0
783 80 -0.18344168 0.0
783 82 -0.092397705 0.0
783 87 -0.029027818 0.0
783 88 -0.15155867 0.0
783 90 -0.09951956 0.0
783 94 0.0007455405 0.0
783 95 -0.07668799 0.0
783 98 -0.2353803 0.0
783 112 0.22917481 0.0
783 113 0.15057087 0.0
783 116 -0.19913436 0.0
783 118 -0.11088969 0.0
783 124 -0.10764146 0.0
783 128 0.21728761 0.0
783 140 -0.095090106 0.0
783 141 0.13155106 0.0
783 148 -0.084194645 0.0
783 150 0.13255519 0.0
783 153 -0.23837946 0.0
783 154 0.055257957 0.0
783 170 -0.18909545 0.0
783 171 -0.2258775 0.0
783 172 -0.2069966 0.0
783 182 -0.12362828 0.0
783 183 0.003649642 0.0
783 185 0.055434905 0.0
783 188 -0.0178259 0.0
783 200 0.017075904 0.0
783 208 0.1167367 0.0
783 211 -0.05640498

In [20]:
to_prune_count

15

In [21]:
test_feed_dict = {x_placeholder:test_images_reshaped,y_placeholder:test_labels,weight_prune_k:1}
sess.run(layer_weights_to_prune,feed_dict=test_feed_dict)

100000